## 0 - Environment preparation

### Install pyenv on WSL

```
# Clone pyenv
curl https://pyenv.run | bash
# Add to your shell startup (e.g. ~/.bashrc or ~/.zshrc):
export PATH="$HOME/.pyenv/bin:$PATH"
eval "$(pyenv init --path)"
eval "$(pyenv init -)"
eval "$(pyenv virtualenv-init -)"
# Then reload:
exec $SHELL
```

### Build Python 3.10.12

```
pyenv install 3.10.12
# Verify:
pyenv versions
```

### Create & activate a pyenv-venv

```
pyenv virtualenv 3.10.12 yakuza_venv
pyenv activate yakuza_venv
```

### Install Jupyter & ipykernel to work with Jypyter Notebooks

```
pip install jupyter ipykernel
```

### Install necessary libraries

```
pip install numpy pandas torch Bio transformers fair-esm xgboost scikit-learn
```

### Download Serratia bacterial genomes from NCBI

```
pip install ncbi-genome-download
ncbi-genome-download \
    --section genbank \
    --formats fasta \
    --assembly-levels complete \
    --species-taxid 615,82996 \
    --output-folder ./data/ncbi_bacteria \
    bacteria
```

### pharokka installation
#### Using pip:
```
pip install pharokka PHANOTATE
git clone https://github.com/gbouras13/pharokka.git
```

#### Alternatively with conda:
```
sudo apt install -y wget git build-essential hmmer barrnap trnascan-se
wget https://repo.anaconda.com/miniconda/Miniconda3-latest-Linux-x86_64.sh
bash Miniconda3-latest-Linux-x86_64.sh
```
#### Restart terminal to finalize conda installation
```
conda env create -f pharokka/environment.yml
conda activate pharokka_env
```

### Install pharokka databases:
```
./pharokka/bin/install_databases.py
```

#### MMseqs2:
```
wget https://github.com/soedinglab/MMseqs2/releases/download/13-45111/mmseqs-linux-avx2.tar.gz
tar xvfz mmseqs-linux-avx2.tar.gz
```

#### MinCED:
```
sudo apt install openjdk-11-jre
sudo apt install openjdk-11-jdk-headless
git clone https://github.com/ctSkennerton/minced.git
cd minced
make
sudo cp minced.jar /usr/local/bin/
sudo cp minced /usr/local/bin/
cd ..
```

#### ARAGORN:
```
mkdir aragorn; cd aragorn
wget https://anaconda.org/bioconda/aragorn/1.2.41/download/linux-64/aragorn-1.2.41-h031d066_3.tar.bz2
tar -xvjf aragorn-1.2.41-h031d066_3.tar.bz2
sudo cp bin/aragorn /usr/local/bin/
cd ..
```

#### Mash:
```
wget https://github.com/marbl/Mash/releases/download/v2.3/mash-Linux64-v2.3.tar
tar -xvf mash-Linux64-v2.3.tar
sudo cp mash-Linux64-v2.3/mash /usr/local/bin/
```

#### Dnaapler:
```
pip3 install dnaapler
```

### Install RBPdetect_v4_ESMfinetuned

```
sudo apt install unzip
wget 'https://zenodo.org/records/14810759/files/RBPdetect_v4_ESMfine.zip?download=1' -O 'RBPdetect_v4_ESMfine.zip'
unzip ./RBPdetect_v4_ESMfine.zip -d .
rm -f RBPdetect_v4_ESMfine.zip
```

### Bakta
#### Using conda (recommended):
```
conda install -c conda-forge -c bioconda bakta
```

#### Using pip (must install 3rd party dependencies manually):
```
pip install bakta
```

##### AMRFinderPlus:
```
mkdir AMRFinderPlus; cd AMRFinderPlus
wget https://github.com/ncbi/amr/releases/download/amrfinder_v4.0.3/amrfinder_binaries_v4.0.3.tar.gz
tar -xvzf amrfinder_binaries_v4.0.3.tar.gz
cd ..
sudo cp ./AMRFinderPlus/* /usr/local/bin/
```

##### PILER-CR:
```
wget http://www.drive5.com/pilercr/pilercr1.06.tar.gz
tar -xvzf pilercr1.06.tar.gz
cd pilercr1.06
make
sudo cp ./pilercr /usr/local/bin/
cd ..
```

##### Diamond:
```
wget https://github.com/bbuchfink/diamond/releases/download/v2.1.10/diamond-linux64.tar.gz
tar -xvzf diamond-linux64.tar.gz
sudo mv diamond /usr/local/bin/
```

##### Blast+ (update from 2.12.0 to 2.14.0):
```
sudo apt remove -y ncbi-blast+
wget https://ftp.ncbi.nlm.nih.gov/blast/executables/blast+/2.14.0/ncbi-blast-2.14.0+-x64-linux.tar.gz
tar -xvzf ncbi-blast-2.14.0+-x64-linux.tar.gz
sudo mv ncbi-blast-2.14.0+/bin/* /usr/local/bin/
```

### Install full database (~30GB):
```
mkdir bakta_db
bakta_db download --output ./bakta_db --type full
```

### Run against a single genome .fasta:
```
mkdir ./data/bakta_test
bakta --db ./bakta_db/db --output ./data/bakta_test --force ./data/bacteria_genomes/33KP-HG.fasta
bakta --db ./bakta_db/db \
      --output ./data/bakta_test \
      --force \
      --skip-trna \
      --skip-tmrna \
      --skip-rrna \
      --skip-ncrna \
      --skip-ncrna-region \
      --skip-crispr \
      --skip-pseudo \
      --skip-sorf \
      --skip-gap \
      --skip-plot \
      ./data/bacteria_genomes/33KP-HG.fasta
```

### In general:
#### For training:
```
bakta --db ./bakta_db/db \
      --output <bakta_output_path> \
      --force \
      --skip-trna \
      --skip-tmrna \
      --skip-rrna \
      --skip-ncrna \
      --skip-ncrna-region \
      --skip-crispr \
      --skip-pseudo \
      --skip-sorf \
      --skip-gap \
      --skip-plot \
      <serratia_genome>.fasta
```

#### For inference:
```
bakta --db <db_path> \
      --output <bakta_output_path> \
      --force \
      <serratia_genome>.fasta
```


### Ray Tune

```
pip install ray[tune]
```

# Training

## 1 - Initial setup

In [40]:
# 1 - INITIAL SETUP
# --------------------------------------------------
import ray
import pickle
import numpy as np
import pandas as pd
from tqdm import tqdm
from pathlib import Path
from ray import tune
from ray.tune.schedulers import ASHAScheduler
from functools import partial
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split, GroupKFold
from sklearn.metrics import roc_auc_score, average_precision_score, f1_score, accuracy_score

import serraphim_processing as sp
import serraphim_features as sf

# Project path
main_path = '/home/sntokos/SerraPHIM'

# General paths
code_path = main_path + '/code'
data_path = main_path + '/data'
results_path = main_path + '/results'

# Bacterial genome data paths
bact_genomes_path = data_path + '/bacteria_genomes'
ncbi_bact_path = data_path + '/ncbi_bacteria/genbank/bacteria'

# Phage genome data and metadata paths
phage_genomes_path = data_path + '/phage_genomes'
phagescope_multiFASTA_path = data_path + '/PhageScope_data/PhageScope_virulent_complete-HQ_sequences.fasta'

phagescope_metadata_path = data_path + '/PhageScope_metadata'
metadata_file = 'serratia_complete-HQ_virulent_phage_metadata.tsv'

data_suffix = '_training'

# Software and database paths
pharokka_executable_path = 'apptainer run /stornext/GL_CARPACCIO/home/HPC/opt/singularity/pharokka-1.7.3.sif pharokka.py'
pharokka_db_path = '/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db'

RBP_detect_model_path = main_path + '/RBPdetect_v4_ESMfine'

bakta_db_path = '/stornext/GL_CARPACCIO/home/HPC/opt/db/bakta-6.0/db'
bakta_results_path = data_path + '/bakta_results'

# Set number of CPUs for all heavy processes
n_cpus = 80

# Paths for testing purposes:
phage_genomes_sample_path = phage_genomes_path + '/sample'
bact_genomes_sample_path = bact_genomes_path + '/sample'

## 2 - Data processing

In [3]:
# 2 - DATA PROCESSING
# --------------------------------------------------

# Check if the bacterial genomes' directory exists and is empty
if not Path(bact_genomes_path).exists() or not any(Path(bact_genomes_path).iterdir()):
    print("Bacterial genomes' directory is empty. Processing NCBI FASTA files...")
    sp.process_ncbi_fasta(
        input_root=ncbi_bact_path,
        output_root=bact_genomes_path,
        combine_plasmids="True"
    )
    # combine_plasmids="True" -> 284 FASTA files saved (plasmid-only FNA files skipped)
    # combine_plasmids="False" -> 578 FASTA files saved
else:
    print("Bacterial genomes' directory is not empty. Moving on...")
    pass

Bacterial genomes' directory is not empty. Moving on...


In [4]:
# Create or load phage metadata
phage_metadata = sp.load_or_create_curated_phage_metadata(
    phagescope_metadata_path,
    metadata_file
)

# Split the multi-FASTA file manually created using PhageScope
if not Path(phage_genomes_path).exists() or not any(Path(phage_genomes_path).iterdir()):
    print("Phage genomes' directory is empty. Processing PhageScope multi-FASTA file...")
    sp.split_fasta_by_phage_id(
        phagescope_multiFASTA_path,
        phage_genomes_path
    )
else:
    print("Phage genomes' directory is not empty. Moving on...")
    pass

Metadata file already exists: serratia_complete-HQ_virulent_phage_metadata.tsv
Phage genomes' directory is not empty. Moving on...


In [5]:
# Derive interaction matrix
interaction_filepath = data_path + f'/interactions/phage_host_interactions{data_suffix}.csv'

phage_host_interaction_matrix = sp.derive_phage_host_interaction_matrix(
    bact_genomes_path,
    phage_metadata,
    interaction_filepath
)

Interaction matrix already exists at: /home/sntokos/SerraPHIM/data/interactions/phage_host_interactions_training.csv


In [13]:
# Run pharokka
sp.pharokka_processing(
    data_path, 
    phage_genomes_path, # phage_genomes_path or phage_genomes_sample_path
    pharokka_executable_path, 
    pharokka_db_path, 
    data_suffix,
    threads=n_cpus  # 128 cores in yakuza server
)

  0%|                                                                                                                                                                                                            | 0/173 [00:00<?, ?it/s]

2025-07-26 13:56:29.239 | INFO     | input_commands:instantiate_dirs:183 - Removing output directory /home/sntokos/SerraPHIM/data/pharokka_results/NC_020083.1 as -f or --force was specified.
2025-07-26 13:56:29.245 | INFO     | __main__:main:95 - Starting Pharokka v1.7.3
2025-07-26 13:56:29.245 | INFO     | __main__:main:96 - Command executed: Namespace(infile='/home/sntokos/SerraPHIM/data/phage_genomes/NC_020083.1.fasta', outdir='/home/sntokos/SerraPHIM/data/pharokka_results/NC_020083.1', database='/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db', threads='80', force=True, prefix='Default', locustag='Default', gene_predictor='default', meta=False, split=False, coding_table='11', evalue='1E-05', fast=False, mmseqs2_only=False, meta_hmm=False, dnaapler=False, custom_hmm='', genbank=False, terminase=False, terminase_strand='nothing', terminase_start='nothing', skip_extra_annotations=False, skip_mash=False, minced_args='', mash_distance=0.2, citation=False)
2025-07-26 13:56:29.246 | IN

  1%|█                                                                                                                                                                                                | 1/173 [01:57<5:37:07, 117.60s/it]

2025-07-26 13:58:26.561 | INFO     | input_commands:instantiate_dirs:183 - Removing output directory /home/sntokos/SerraPHIM/data/pharokka_results/Station38_MES_ALL_assembly_NODE_158_length_44738_cov_6.876799 as -f or --force was specified.
2025-07-26 13:58:26.577 | INFO     | __main__:main:95 - Starting Pharokka v1.7.3
2025-07-26 13:58:26.577 | INFO     | __main__:main:96 - Command executed: Namespace(infile='/home/sntokos/SerraPHIM/data/phage_genomes/Station38_MES_ALL_assembly_NODE_158_length_44738_cov_6.876799.fasta', outdir='/home/sntokos/SerraPHIM/data/pharokka_results/Station38_MES_ALL_assembly_NODE_158_length_44738_cov_6.876799', database='/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db', threads='80', force=True, prefix='Default', locustag='Default', gene_predictor='default', meta=False, split=False, coding_table='11', evalue='1E-05', fast=False, mmseqs2_only=False, meta_hmm=False, dnaapler=False, custom_hmm='', genbank=False, terminase=False, terminase_strand='nothing', ter

  1%|██▏                                                                                                                                                                                               | 2/173 [03:04<4:10:36, 87.93s/it]

...

2025-07-26 17:13:30.908 | INFO     | input_commands:instantiate_dirs:183 - Removing output directory /home/sntokos/SerraPHIM/data/pharokka_results/Station100_DCM_ALL_assembly_NODE_335_length_37603_cov_12.418504 as -f or --force was specified.
2025-07-26 17:13:30.914 | INFO     | __main__:main:95 - Starting Pharokka v1.7.3
2025-07-26 17:13:30.914 | INFO     | __main__:main:96 - Command executed: Namespace(infile='/home/sntokos/SerraPHIM/data/phage_genomes/Station100_DCM_ALL_assembly_NODE_335_length_37603_cov_12.418504.fasta', outdir='/home/sntokos/SerraPHIM/data/pharokka_results/Station100_DCM_ALL_assembly_NODE_335_length_37603_cov_12.418504', database='/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db', threads='80', force=True, prefix='Default', locustag='Default', gene_predictor='default', meta=False, split=False, coding_table='11', evalue='1E-05', fast=False, mmseqs2_only=False, meta_hmm=False, dnaapler=False, custom_hmm='', genbank=False, terminase=False, terminase_strand='nothing

 99%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉ | 172/173 [3:18:01<01:07, 67.54s/it]

2025-07-26 17:14:30.981 | INFO     | input_commands:instantiate_dirs:183 - Removing output directory /home/sntokos/SerraPHIM/data/pharokka_results/NC_054938.1 as -f or --force was specified.
2025-07-26 17:14:30.989 | INFO     | __main__:main:95 - Starting Pharokka v1.7.3
2025-07-26 17:14:30.989 | INFO     | __main__:main:96 - Command executed: Namespace(infile='/home/sntokos/SerraPHIM/data/phage_genomes/NC_054938.1.fasta', outdir='/home/sntokos/SerraPHIM/data/pharokka_results/NC_054938.1', database='/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db', threads='80', force=True, prefix='Default', locustag='Default', gene_predictor='default', meta=False, split=False, coding_table='11', evalue='1E-05', fast=False, mmseqs2_only=False, meta_hmm=False, dnaapler=False, custom_hmm='', genbank=False, terminase=False, terminase_strand='nothing', terminase_start='nothing', skip_extra_annotations=False, skip_mash=False, minced_args='', mash_distance=0.2, citation=False)
2025-07-26 17:14:30.989 | IN

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 173/173 [3:19:31<00:00, 69.20s/it]

Pharokka processing complete.


In [5]:
# Run RBP detection using PhageRBPdetect_v4
# WARNING: No GPUs in yakuza server!
sp.process_and_detect_rbps_v4(
    data_path, 
    RBP_detect_model_path, 
    data_suffix,
    gpu_index=0,
    threads=n_cpus  # 128 cores in yakuza server
)

Using device: cpu (with 80 threads if CPU)


Processing phages:   0%|                                                                                                                                                                                                  | 0/173 [00:00<?, ?it/s]
Inference for Station188_DCM_ALL_assembly_NODE_932_length_43282_cov_7.321743:   0%|                                                                                                                                        | 0/68 [00:00<?, ?it/s]Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.

Inference for Station188_DCM_ALL_assembly_NODE_932_length_43282_cov_7.321743:   1%|█▉                                                                                                                              | 1/68 [00:18<20:06, 18.00s/it]
Inference for Station188_DCM_ALL_assembly_NODE_932_length_43282_cov_7.321743:   4%|█████▋                                         

RBP detection complete. Results saved to 'RBPbase_training.csv'


In [5]:
# Run Bakta
product_keywords = [
    "capsule", "polysaccharide", "-polysaccharide", "LPS",
    "oligosaccharide polymerase",
    "UDP-", "GDP-",
    "mannose",
    "guanylyltransferase",
    "glycosyltransferase",
    "flippase",
    "-antigen", "O-antigen",
    "outer membrane", "outer core", "omp-",
    "mannosyltransferase",
    "fimbria-",
    "pili-", "pilus",
    "adhesin",
    "cellulose",
    "curli",
    # "receptor", # too generic? any receptors not related to surface receptors? 
    "siderophore receptor", "siderophore",
    "enterobactin receptor",
    "aerobactin receptor",
    "yersiniabactin receptor",
    "salmochelin receptor",
    "phage receptor",
    # "prophage", # how is a possible prophage existence affecting the susceptibility to other phages?
    # "phage", "tail fiber", # + other phage components... (CDS in prophage regions?)
    "porin", "-porin",
    "efflux pump",
    "hemagglutinin", "haemagglutinin",
    "lectin",
    "lipid", "-lipid", 
    # "lipoprotein", # too generic? any lipoproteins not related to cell wall / surface receptors?
    "beta-barrel assembly",
    "autotransporter",
    "pathway protein",
    "flagell-",
    "chemotaxis",
    "transporter membrane", "transmembrane",
    "TonB-dependent receptor", "TonB", "TonB-",
    "chitinase", "lecithinase", "hemolysin", 
    "lipase", "-lipase", 
    "protease", "-protease",
    "exoenzyme-", "virulence", "invasion"
]
gene_keywords = [
    "wza", # (capsule export)
    "wzb", # (tyrosine-protein phosphatase)
    "wzc", # (capsule synthesis tyrosine kinase)
    "galF", # (UDP-glucose pyrophosphorylase)
    "ugd", # (UDP-glucose dehydrogenase)
    "manC", # (GDP-mannose pyrophosphorylase)
    "manB", # (mannose-1-phosphate guanylyltransferase)
    "Wzx", # (O-antigen flippase)
    "Wzy", # (O-antigen polymerase)
    "WaaL", # (O-antigen ligase)
    "Waa-", # (core LPS biosynthesis)
    #"magA", # (K1-specific capsular serotype proteins)
    #"rmpA", # (K2-specific capsular serotype proteins)
    "OmpA", "OmpX", "Omp-", # (outer membrane proteins)
    #"OmpK-", # (Klebsiella-specific outer membrane proteins)
    "TolC", # (outer membrane proteins)
    "OprD", "Opr-", # (outer membrane proteins)
    "HasR", "HasB", # (TonB-dependent outer membrane receptor complex)
    "lpx-", # (lipid A biosynthesis: lpxA, lpxC, lpxD)
    "WbbP", # (mannosyltransferase)
    "fimA", "fimH", # (Type 1 fimbriae)
    "mrkA", "mrkB", "mrkC", # (Type 3 fimbriae)
    "PilQ", "PilX", # (Adhesins)
    "csgA", "csgB", # (Curli fibers)
    "FliD", # (Flagellar hook-associated proteins)
    "CheA", "CheB", "CheR", "CheY", "CheW", "CheZ", "Che-", # (Chemotaxis proteins)
    "FepA", "Fiu", # (Enterobactin receptors)
    "IutA", # (Aerobactin receptors)
    "FyuA", # (Yersiniabactin receptors)
    "IroN" # (Salmochelin receptors)
]
sp.run_bakta_and_extract_receptors(
    bact_genomes_path, # 'bact_genomes_path' or 'bact_genomes_sample_path'
    bakta_results_path, 
    bakta_db_path, 
    gene_keywords, product_keywords,
    data_suffix,
    threads=n_cpus,  # 128 cores in yakuza server
    training=True
)

Processing genomes:   0%|                                                                                                  | 0/284 [00:00<?, ?it/s]

Skipping Bakta for CP163149.1_Serratia_marcescens_strain_A26716_chromosome: output already exists.
Receptor genes:      Sequence Id Type    Start     Stop Strand     Locus Tag  Gene  \
10      contig_1  cds     8627    10000      +  BNADPM_00011  glmU   
18      contig_1  cds    17958    18671      +  BNADPM_00019  hisM   
54      contig_1  cds    55462    56124      -  BNADPM_00054  ompA   
57      contig_1  cds    57586    59574      +  BNADPM_00057  estA   
102     contig_1  cds   104617   106062      +  BNADPM_00102  tolC   
...          ...  ...      ...      ...    ...           ...   ...   
4647    contig_1  cds  5112142  5113155      -  BNADPM_04647  rfaF   
4648    contig_1  cds  5113281  5114558      +  BNADPM_04648  waaA   
4649    contig_1  cds  5114559  5115332      +  BNADPM_04649  kdtX   
4675    contig_1  cds  5138774  5139667      -  BNADPM_04675  brkB   
4690    contig_1  cds  5157405  5157995      +  BNADPM_04690  mobA   

                                            

Processing genomes:   0%|▎                                                                                         | 1/284 [00:01<07:31,  1.59s/it]

Skipping Bakta for CP071188.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S94_jyu2015_chromosome_+_plasmids: output already exists.
Receptor genes:      Sequence Id Type  Start   Stop Strand     Locus Tag  Gene  \
20      contig_1  cds  23517  24179      -  JDDDIC_00021  ompA   
23      contig_1  cds  25638  27626      +  JDDDIC_00024  estA   
77      contig_1  cds  81646  82443      -  JDDDIC_00078   NaN   
78      contig_1  cds  82876  83412      +  JDDDIC_00079   NaN   
79      contig_1  cds  83517  84053      +  JDDDIC_00080   NaN   
...          ...  ...    ...    ...    ...           ...   ...   
4729    contig_2  cds  27962  28276      +  JDDDIC_04729  traQ   
4730    contig_2  cds  28263  28799      +  JDDDIC_04730  trbB   
4731    contig_2  cds  28796  30163      +  JDDDIC_04731  traH   
4738    contig_2  cds  41519  42073      +  JDDDIC_04738   NaN   
4739    contig_2  cds  42087  42869      +  JDDDIC_04739  traX   

                                           

Processing genomes:   1%|▋                                                                                         | 2/284 [00:02<05:26,  1.16s/it]

...

Command: apptainer exec --env MPLBACKEND=Agg /stornext/GL_CARPACCIO/home/HPC/opt/singularity/bakta-1.11.0.sif bakta --db /stornext/GL_CARPACCIO/home/HPC/opt/db/bakta-6.0/db --output /home/sntokos/SerraPHIM/data/bakta_results/CP071226.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S22_jyu2015_chromosome_+_plasmids --force --threads 80 --skip-trna --skip-tmrna --skip-rrna --skip-ncrna --skip-ncrna-region --skip-crispr --skip-pseudo --skip-sorf --skip-gap --skip-plot /home/sntokos/SerraPHIM/data/bacteria_genomes/CP071226.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S22_jyu2015_chromosome_+_plasmids.fasta
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:558: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:90: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'>

Processing genomes: 100%|███████████████████████████████████████████████████████████████████████████████████▋| 283/284 [16:37:31<04:15, 255.82s/it]

Command: apptainer exec --env MPLBACKEND=Agg /stornext/GL_CARPACCIO/home/HPC/opt/singularity/bakta-1.11.0.sif bakta --db /stornext/GL_CARPACCIO/home/HPC/opt/db/bakta-6.0/db --output /home/sntokos/SerraPHIM/data/bakta_results/CP071208.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S81_jyu2015_chromosome_+_plasmids --force --threads 80 --skip-trna --skip-tmrna --skip-rrna --skip-ncrna --skip-ncrna-region --skip-crispr --skip-pseudo --skip-sorf --skip-gap --skip-plot /home/sntokos/SerraPHIM/data/bacteria_genomes/CP071208.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S81_jyu2015_chromosome_+_plasmids.fasta
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:558: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:90: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'>

Processing genomes: 100%|████████████████████████████████████████████████████████████████████████████████████| 284/284 [16:41:30<00:00, 211.59s/it]


Receptor extraction complete. Results saved to /home/sntokos/SerraPHIM/data/bakta_results/Bact_receptors_training.json and /home/sntokos/SerraPHIM/data/bakta_results/Bact_receptors_verbose_training.json


## 3 - Feature construction

In [6]:
# 3 - FEATURE CONSTRUCTION
# --------------------------------------------------

# ESM-2 features for RBPs
sf.compute_esm2_embeddings_rbp_improved(
    data_path, 
    data_suffix, 
    batch_size=n_cpus
)

Downloading: "https://dl.fbaipublicfiles.com/fair-esm/models/esm2_t33_650M_UR50D.pt" to /home/sntokos/.cache/torch/hub/checkpoints/esm2_t33_650M_UR50D.pt
Downloading: "https://dl.fbaipublicfiles.com/fair-esm/regression/esm2_t33_650M_UR50D-contact-regression.pt" to /home/sntokos/.cache/torch/hub/checkpoints/esm2_t33_650M_UR50D-contact-regression.pt


Embedding sequences: 100%|████████████████████████████████████████████████████████████████| 299/299 [15:47<00:00,  3.17s/it]


Saved embeddings to /home/sntokos/SerraPHIM/data/esm2_embeddings_rbp_training.csv


In [7]:
# ESM-2 features for bacterial receptors 
sf.compute_esm2_embeddings_receptors(
    data_path, 
    bakta_results_path, 
    data_suffix,
    aggregate_by_accession=True,  # Set to true during internship
    batch_size=n_cpus,
    skip_long_seq=False
)

Will process CP163149.1_Serratia_marcescens_strain_A26716_chromosome_184 solo (length=3548 AA)
Will process CP163149.1_Serratia_marcescens_strain_A26716_chromosome_370 solo (length=1608 AA)
Will process CP071188.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S94_jyu2015_chromosome_+_plasmids_202 solo (length=3550 AA)
Will process CP071188.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S94_jyu2015_chromosome_+_plasmids_370 solo (length=1608 AA)
Will process CP071200.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S96_jyu2015_chromosome_+_plasmids_202 solo (length=3550 AA)
Will process CP071200.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S96_jyu2015_chromosome_+_plasmids_370 solo (length=1608 AA)
Will process CP127881.1_Serratia_marcescens_strain_ELP1.10_chromosome_+_plasmids_366 solo (length=1607 AA)
Will process CP071230.1_Serratia_marcescens_subsp._marcescens_ATCC_13880_substr._Sm_S40_jyu2015_chromosome_+_plasmids_201 solo 

Embedding batches: 100%|██████████████████████████████████████████████████████████████████| 539/539 [59:23<00:00,  6.61s/it]


Saved embeddings to: /home/sntokos/SerraPHIM/data/esm2_embeddings_receptors_training.csv


In [6]:
# Construct feature matrices
rbp_embeddings_path = data_path + '/esm2_embeddings_rbp' + data_suffix + '.csv'
receptors_embeddings_path = data_path + '/esm2_embeddings_receptors' + data_suffix + '.csv'
interaction_path = data_path + '/interactions'

features_esm2, labels, groups_receptors, groups_phage = sf.construct_feature_matrices_receptors(
    interaction_path, 
    data_suffix, 
    receptors_embeddings_path, 
    rbp_embeddings_path
)

Building feature matrix: 100%|██████████████████████████████████████████████████████| 34364/34364 [00:27<00:00, 1259.49it/s]


## 4 - Training & evaluating model

In [23]:
# 4 - TRAINING & EVALUATING MODEL
# --------------------------------------------------

X_full = features_esm2
y_full = labels
groups_receptors = np.array(groups_receptors)
groups_phage = np.array(groups_phage)

imbalance = np.sum(y_full == 1) / np.sum(y_full == 0)
scale_pos_weight_fixed = 1 / imbalance

In [14]:
search_space = {
    "learning_rate": tune.loguniform(1e-3, 0.3),
    "max_depth": tune.choice([3, 5, 7, 9]),
    "n_estimators": tune.choice([100, 200, 300]),
    "scale_pos_weight": scale_pos_weight_fixed,
    "subsample": tune.uniform(0.6, 1.0),
    "colsample_bytree": tune.uniform(0.6, 1.0)
}

def train_xgb_tune(config, X, y):
    # Stratified train/test split
    X_train, X_val, y_train, y_val = train_test_split(
        X, y, test_size=0.2, stratify=y, random_state=42
    )

    model = XGBClassifier(
        learning_rate=config["learning_rate"],
        max_depth=config["max_depth"],
        n_estimators=config["n_estimators"],
        scale_pos_weight=config["scale_pos_weight"],
        subsample=config["subsample"],
        colsample_bytree=config["colsample_bytree"],
        eval_metric="logloss",
        use_label_encoder=False,
        n_jobs=n_cpus
    )
    model.fit(X_train, y_train)
    preds = model.predict_proba(X_val)[:, 1]
    auc = roc_auc_score(y_val, preds)
    
    tune.report({"auc": auc})

In [15]:
ray.shutdown()

In [16]:
ray.init(
    num_cpus=n_cpus,
    _memory=400 * 1024 * 1024 * 1024,  # 400 GB RAM
    ignore_reinit_error=True
)

2025-07-30 17:46:28,896	INFO worker.py:1927 -- Started a local Ray instance.


RayContext(dashboard_url='', python_version='3.10.12', ray_version='2.48.0', ray_commit='03491225d59a1ffde99c3628969ccf456be13efd')

(train_xgb_tune pid=2248986) [17:52:01] WARNING: /workspace/src/learner.cc:738: 
(train_xgb_tune pid=2248986) Parameters: { "use_label_encoder" } are not used.
(train_xgb_tune pid=2248986) 
(train_xgb_tune pid=2250334) 
(train_xgb_tune pid=2250334) [17:52:54] WARNING: /workspace/src/learner.cc:738: 
(train_xgb_tune pid=2250334) Parameters: { "use_label_encoder" } are not used.
(train_xgb_tune pid=2251723) [17:53:57] WARNING: /workspace/src/learner.cc:738: 
(train_xgb_tune pid=2251723) Parameters: { "use_label_encoder" } are not used.
(train_xgb_tune pid=2251723) 
(train_xgb_tune pid=2252960) 
(train_xgb_tune pid=2252960) [17:54:53] WARNING: /workspace/src/learner.cc:738: 
(train_xgb_tune pid=2252960) Parameters: { "use_label_encoder" } are not used.
(train_xgb_tune pid=2254168) [17:55:39] WARNING: /workspace/src/learner.cc:738: 
(train_xgb_tune pid=2254168) Parameters: { "use_label_encoder" } are not used.
(train_xgb_tune pid=2254168) 
(train_xgb_tune pid=2255324) 
(train_xgb_tune pid=

In [17]:
trainable = tune.with_parameters(train_xgb_tune, X=X_full, y=y_full)

analysis = tune.run(
    trainable,
    config=search_space,
    num_samples=100,  # increase for more exhaustive search
    metric="auc",
    mode="max",
    scheduler=ASHAScheduler(max_t=50, grace_period=5),
    resources_per_trial={"cpu": n_cpus},
    storage_path=f"{data_path}/ray_tune_results",
    name="xgb_receptor_tune"
)

2025-07-30 17:51:19,403	INFO tune.py:616 -- [output] This uses the legacy output and progress reporter, as Jupyter notebooks are not supported by the new engine, yet. For more information, please see https://github.com/ray-project/ray/issues/36949


2025-07-30 19:18:41,364	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/home/sntokos/SerraPHIM/data/ray_tune_results/xgb_receptor_tune' in 0.1208s.
2025-07-30 19:18:41,384	INFO tune.py:1041 -- Total run time: 5241.98 seconds (5241.82 seconds for the tuning loop).


In [18]:
best_config = analysis.get_best_config(metric="auc", mode="max")
print("Best hyperparameters:", best_config)

# Train final model using best config
best_model = XGBClassifier(
    **best_config,
    eval_metric='logloss',
    use_label_encoder=False,
    n_jobs=n_cpus
)
best_model.fit(X_full, y_full)
best_model.save_model(f"{results_path}/xgb_receptor_model_tuned{data_suffix}.json")

Best hyperparameters: {'learning_rate': 0.05598257194138915, 'max_depth': 5, 'n_estimators': 100, 'scale_pos_weight': np.float64(0.13244356566155874), 'subsample': 0.9810950232098106, 'colsample_bytree': 0.6903045315589389}


/home/sntokos/serraphim_venv/lib/python3.10/site-packages/xgboost/training.py:183: UserWarning: [19:37:08] WARNING: /workspace/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


In [19]:
# GROUP STRATEGY — choose one of: 'receptor', 'phage', or 'both'
group_by = 'receptor'

if group_by == 'receptor':
    groups = np.array(groups_receptors)
elif group_by == 'phage':
    groups = np.array(groups_phage)
elif group_by == 'both':
    # Optional: define each group as a (phage, receptor) pair
    groups = np.array([f"{b}_{p}" for b, p in zip(groups_receptors, groups_phage)])
else:
    raise ValueError("Invalid grouping strategy selected.")

print(f"Number of unique groups: {len(set(groups))}")

Number of unique groups: 284


In [20]:
# Convert group names to numeric codes (required for splitting)
unique_groups = list(set(groups))
group_to_id = {g: i for i, g in enumerate(unique_groups)}
group_ids = np.array([group_to_id[g] for g in groups])

k = 5
gkf = GroupKFold(n_splits=k)
results = []
true_labels = []

for train_idx, test_idx in tqdm(gkf.split(X_full, y_full, groups=group_ids), total=k):
    X_train, X_test = X_full[train_idx], X_full[test_idx]
    y_train, y_test = y_full[train_idx], y_full[test_idx]

    imbalance = np.sum(y_train == 1) / np.sum(y_train == 0)
    best_config["scale_pos_weight"] = 1 / imbalance
    
    xgb = XGBClassifier(
        **best_config,
        n_jobs=n_cpus,
        eval_metric='logloss',
        use_label_encoder=False
    )
    xgb.fit(X_train, y_train)
    y_score = xgb.predict_proba(X_test)[:, 1]

    results.append(y_score)
    true_labels.append(y_test)

# Save results
with open(f"{results_path}/serr_receptor_level_kfold_results.pickle", "wb") as f:
    pickle.dump({'scores': results, 'labels': true_labels}, f)

  0%|                                                                                                 | 0/5 [00:00<?, ?it/s]/home/sntokos/serraphim_venv/lib/python3.10/site-packages/xgboost/training.py:183: UserWarning: [19:37:46] WARNING: /workspace/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
 20%|█████████████████▊                                                                       | 1/5 [00:11<00:46, 11.73s/it]/home/sntokos/serraphim_venv/lib/python3.10/site-packages/xgboost/training.py:183: UserWarning: [19:37:58] WARNING: /workspace/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)
 40%|███████████████████████████████████▌                                                     | 2/5 [00:23<00:34, 11.60s/it]/home/sntokos/serraphim_venv/lib/python3.10/site-packages/xgboost/training.py:183: UserWarning: [19:38:09] WARNING: /workspace/src/learner.cc:

In [21]:
print("\nPredicted Scores (results):")
for i, arr in enumerate(results):
    print(f"Fold {i+1}: {np.array2string(arr, precision=4, separator=', ', floatmode='fixed')}")

print("\nGround Truth (true_labels):")
for i, arr in enumerate(true_labels):
    print(f"Fold {i+1}: {np.array2string(arr, separator=', ')}")


Predicted Scores (results):
Fold 1: [0.9964, 0.9959, 0.9958, ..., 0.0030, 0.9972, 0.9902]
Fold 2: [0.9941, 0.9947, 0.9942, ..., 0.0036, 0.9468, 0.9601]
Fold 3: [0.9950, 0.9952, 0.9951, ..., 0.0030, 0.9717, 0.9559]
Fold 4: [0.9931, 0.9908, 0.9919, ..., 0.0060, 0.9449, 0.8973]
Fold 5: [0.9967, 0.9957, 0.9957, ..., 0.0070, 0.9516, 0.9558]

Ground Truth (true_labels):
Fold 1: [1, 1, 1, ..., 0, 1, 1]
Fold 2: [1, 1, 1, ..., 0, 1, 1]
Fold 3: [1, 1, 1, ..., 0, 1, 1]
Fold 4: [1, 1, 1, ..., 0, 1, 1]
Fold 5: [1, 1, 1, ..., 0, 1, 1]


In [22]:
# Flatten predictions and labels
all_scores = np.concatenate(results)
all_labels = np.concatenate(true_labels)

# Threshold scores to get predicted classes (you can tune threshold later)
y_pred = (all_scores >= 0.5).astype(int)

# Compute metrics
roc_auc = roc_auc_score(all_labels, all_scores)
pr_auc = average_precision_score(all_labels, all_scores)
f1 = f1_score(all_labels, y_pred)
acc = accuracy_score(all_labels, y_pred)

print("Cross-Validation Metrics:")
print(f"ROC AUC:     {roc_auc:.4f}")
print(f"PR AUC:      {pr_auc:.4f}")
print(f"F1 Score:    {f1:.4f}")
print(f"Accuracy:    {acc:.4f}")

Cross-Validation Metrics:
ROC AUC:     0.8807
PR AUC:      0.9796
F1 Score:    0.9565
Accuracy:    0.9211


# Inference

## 5 - Inference setup

In [42]:
# 5 - INITIAL SETUP
# (same as "1 - INITIAL SETUP" with the following additions)
# --------------------------------------------------

data_inf_path = data_path + '/inference_data'
phage_genomes_inf_path = data_inf_path + '/phage_genomes'
bact_genomes_inf_path = data_inf_path + '/bacteria_genomes'
bakta_inf_results_path = data_inf_path + '/bakta_results'

data_suffix = '_inference'

## 6 - Inference data processing

In [ ]:
# 6 - DATA PROCESSING
# --------------------------------------------------

# Run pharokka
sp.pharokka_processing(
    data_inf_path, 
    phage_genomes_inf_path, 
    pharokka_executable_path, 
    pharokka_db_path, 
    data_suffix,
    threads=n_cpus  # 128 cores in yakuza server
)

  0%|                                                                                                | 0/15 [00:00<?, ?it/s]

2025-07-30 20:23:28.547 | INFO     | input_commands:instantiate_dirs:183 - Removing output directory /home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_26_reoriented as -f or --force was specified.
2025-07-30 20:23:28.554 | INFO     | __main__:main:95 - Starting Pharokka v1.7.3
2025-07-30 20:23:28.554 | INFO     | __main__:main:96 - Command executed: Namespace(infile='/home/sntokos/SerraPHIM/data/inference_data/phage_genomes/dv_26_reoriented.fasta', outdir='/home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_26_reoriented', database='/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db', threads='80', force=True, prefix='Default', locustag='Default', gene_predictor='default', meta=False, split=False, coding_table='11', evalue='1E-05', fast=False, mmseqs2_only=False, meta_hmm=False, dnaapler=False, custom_hmm='', genbank=False, terminase=False, terminase_strand='nothing', terminase_start='nothing', skip_extra_annotations=False, skip_mash=False, minced_args='', mas

  7%|█████▊                                                                                 | 1/15 [02:51<40:07, 171.97s/it]

2025-07-30 20:26:19.915 | INFO     | input_commands:instantiate_dirs:183 - Removing output directory /home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_142 as -f or --force was specified.
2025-07-30 20:26:19.921 | INFO     | __main__:main:95 - Starting Pharokka v1.7.3
2025-07-30 20:26:19.921 | INFO     | __main__:main:96 - Command executed: Namespace(infile='/home/sntokos/SerraPHIM/data/inference_data/phage_genomes/dv_142.fasta', outdir='/home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_142', database='/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db', threads='80', force=True, prefix='Default', locustag='Default', gene_predictor='default', meta=False, split=False, coding_table='11', evalue='1E-05', fast=False, mmseqs2_only=False, meta_hmm=False, dnaapler=False, custom_hmm='', genbank=False, terminase=False, terminase_strand='nothing', terminase_start='nothing', skip_extra_annotations=False, skip_mash=False, minced_args='', mash_distance=0.2, citation=False

 13%|███████████▌                                                                           | 2/15 [04:37<28:44, 132.68s/it]

...

2025-07-30 20:46:41.185 | INFO     | external_tools:run:52 - Done running phanotate.py -f fasta -o /home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_53_1_reoriented/phanotate_out_tmp.fasta /home/sntokos/SerraPHIM/data/inference_data/phage_genomes/dv_53_1_reoriented.fasta
2025-07-30 20:46:41.187 | INFO     | external_tools:run:50 - Started running phanotate.py -f tabular -o /home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_53_1_reoriented/phanotate_out.txt /home/sntokos/SerraPHIM/data/inference_data/phage_genomes/dv_53_1_reoriented.fasta ...
2025-07-30 20:47:38.661 | INFO     | external_tools:run:52 - Done running phanotate.py -f tabular -o /home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_53_1_reoriented/phanotate_out.txt /home/sntokos/SerraPHIM/data/inference_data/phage_genomes/dv_53_1_reoriented.fasta
2025-07-30 20:47:38.757 | INFO     | __main__:main:309 - Starting tRNA-scanSE.
2025-07-30 20:47:38.758 | INFO     | external_tools:run:50 - Sta

 93%|████████████████████████████████████████████████████████████████████████████████▎     | 14/15 [25:00<01:54, 114.57s/it]

2025-07-30 20:48:28.734 | INFO     | input_commands:instantiate_dirs:183 - Removing output directory /home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_55_1_reoriented as -f or --force was specified.
2025-07-30 20:48:28.740 | INFO     | __main__:main:95 - Starting Pharokka v1.7.3
2025-07-30 20:48:28.740 | INFO     | __main__:main:96 - Command executed: Namespace(infile='/home/sntokos/SerraPHIM/data/inference_data/phage_genomes/dv_55_1_reoriented.fasta', outdir='/home/sntokos/SerraPHIM/data/inference_data/pharokka_results/dv_55_1_reoriented', database='/stornext/GL_CARPACCIO/home/HPC/opt/db/pharokka-db', threads='80', force=True, prefix='Default', locustag='Default', gene_predictor='default', meta=False, split=False, coding_table='11', evalue='1E-05', fast=False, mmseqs2_only=False, meta_hmm=False, dnaapler=False, custom_hmm='', genbank=False, terminase=False, terminase_strand='nothing', terminase_start='nothing', skip_extra_annotations=False, skip_mash=False, minced_args='

100%|██████████████████████████████████████████████████████████████████████████████████████| 15/15 [27:15<00:00, 109.01s/it]


Pharokka processing complete.


In [ ]:
sp.process_and_detect_rbps_v4(
    data_inf_path, 
    RBP_detect_model_path, 
    data_suffix,
    gpu_index=0,
    threads=n_cpus  # 128 cores in yakuza server
)

Using device: cpu (with 80 threads if CPU)


Inference for dv_81_1_reoriented:   0%|                                                             | 0/307 [00:00<?, ?it/s]Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.

Processing phages: 100%|████████████████████████████████████████████████████████████████████| 15/15 [02:27<00:00,  9.82s/it]

RBP detection complete. Results saved to 'RBPbase_inference.csv'


In [34]:
# Run Bakta
product_keywords = [
    "capsule", "polysaccharide", "-polysaccharide", "LPS",
    "oligosaccharide polymerase",
    "UDP-", "GDP-",
    "mannose",
    "guanylyltransferase",
    "glycosyltransferase",
    "flippase",
    "-antigen", "O-antigen",
    "outer membrane", "outer core", "omp-",
    "mannosyltransferase",
    "fimbria-",
    "pili-", "pilus",
    "adhesin",
    "cellulose",
    "curli",
    # "receptor", # too generic? any receptors not related to surface receptors? 
    "siderophore receptor", "siderophore",
    "enterobactin receptor",
    "aerobactin receptor",
    "yersiniabactin receptor",
    "salmochelin receptor",
    "phage receptor",
    # "prophage", # how is a possible prophage existence affecting the susceptibility to other phages?
    # "phage", "tail fiber", # + other phage components... (CDS in prophage regions?)
    "porin", "-porin",
    "efflux pump",
    "hemagglutinin", "haemagglutinin",
    "lectin",
    "lipid", "-lipid", 
    # "lipoprotein", # too generic? any lipoproteins not related to cell wall / surface receptors?
    "beta-barrel assembly",
    "autotransporter",
    "pathway protein",
    "flagell-",
    "chemotaxis",
    "transporter membrane", "transmembrane",
    "TonB-dependent receptor", "TonB", "TonB-",
    "chitinase", "lecithinase", "hemolysin", 
    "lipase", "-lipase", 
    "protease", "-protease",
    "exoenzyme-", "virulence", "invasion"
]
gene_keywords = [
    "wza", # (capsule export)
    "wzb", # (tyrosine-protein phosphatase)
    "wzc", # (capsule synthesis tyrosine kinase)
    "galF", # (UDP-glucose pyrophosphorylase)
    "ugd", # (UDP-glucose dehydrogenase)
    "manC", # (GDP-mannose pyrophosphorylase)
    "manB", # (mannose-1-phosphate guanylyltransferase)
    "Wzx", # (O-antigen flippase)
    "Wzy", # (O-antigen polymerase)
    "WaaL", # (O-antigen ligase)
    "Waa-", # (core LPS biosynthesis)
    #"magA", # (K1-specific capsular serotype proteins)
    #"rmpA", # (K2-specific capsular serotype proteins)
    "OmpA", "OmpX", "Omp-", # (outer membrane proteins)
    #"OmpK-", # (Klebsiella-specific outer membrane proteins)
    "TolC", # (outer membrane proteins)
    "OprD", "Opr-", # (outer membrane proteins)
    "HasR", "HasB", # (TonB-dependent outer membrane receptor complex)
    "lpx-", # (lipid A biosynthesis: lpxA, lpxC, lpxD)
    "WbbP", # (mannosyltransferase)
    "fimA", "fimH", # (Type 1 fimbriae)
    "mrkA", "mrkB", "mrkC", # (Type 3 fimbriae)
    "PilQ", "PilX", # (Adhesins)
    "csgA", "csgB", # (Curli fibers)
    "FliD", # (Flagellar hook-associated proteins)
    "CheA", "CheB", "CheR", "CheY", "CheW", "CheZ", "Che-", # (Chemotaxis proteins)
    "FepA", "Fiu", # (Enterobactin receptors)
    "IutA", # (Aerobactin receptors)
    "FyuA", # (Yersiniabactin receptors)
    "IroN" # (Salmochelin receptors)
]

sp.run_bakta_and_extract_receptors(
    bact_genomes_inf_path, 
    bakta_inf_results_path, 
    bakta_db_path, 
    gene_keywords, product_keywords,
    data_suffix,
    threads=n_cpus,  # 128 cores in yakuza server
    training=False
)

Processing genomes:   0%|                                                                             | 0/3 [00:00<?, ?it/s]

Command: apptainer exec --env MPLBACKEND=Agg /stornext/GL_CARPACCIO/home/HPC/opt/singularity/bakta-1.11.0.sif bakta --db /stornext/GL_CARPACCIO/home/HPC/opt/db/bakta-6.0/db --output /home/sntokos/SerraPHIM/data/inference_data/bakta_results/EIF4 --force --threads 80 /home/sntokos/SerraPHIM/data/inference_data/bacteria_genomes/EIF4.fasta
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:558: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:90: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  return self._float_to_str(self.smallest_subnormal)
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:558: UserWarning: The value of the smallest subnormal for <class 'numpy.float64'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/usr/local/lib/python

Processing genomes:  33%|██████████████████████▋                                             | 1/3 [09:10<18:21, 550.67s/it]

Receptor genes:      Sequence Id Type  Start   Stop Strand     Locus Tag  Gene  \
22      contig_1  cds  23881  24540      -  OKLPFL_00023  ompA   
25      contig_1  cds  25869  27857      +  OKLPFL_00026   NaN   
79      contig_1  cds  82865  83824      -  OKLPFL_00079   NaN   
83      contig_1  cds  87442  88623      +  OKLPFL_00083  wecB   
92      contig_1  cds  98487  99881      +  OKLPFL_00092   NaN   
...          ...  ...    ...    ...    ...           ...   ...   
5346    contig_2  cds  34932  35930      -  OKLPFL_05262  traU   
5355    contig_2  cds  42029  43423      -  OKLPFL_05271  traB   
5359    contig_2  cds  45035  45406      -  OKLPFL_05275  traA   
5377    contig_2  cds  61191  67073      -  OKLPFL_05293   NaN   
5378    contig_2  cds  67149  68792      -  OKLPFL_05294   NaN   

                                                Product  \
22                              OmpA family lipoprotein   
25                                             Lipase 1   
79            

Processing genomes:  67%|█████████████████████████████████████████████▎                      | 2/3 [18:29<09:15, 555.52s/it]

Command: apptainer exec --env MPLBACKEND=Agg /stornext/GL_CARPACCIO/home/HPC/opt/singularity/bakta-1.11.0.sif bakta --db /stornext/GL_CARPACCIO/home/HPC/opt/db/bakta-6.0/db --output /home/sntokos/SerraPHIM/data/inference_data/bakta_results/LVF4 --force --threads 80 /home/sntokos/SerraPHIM/data/inference_data/bacteria_genomes/LVF4.fasta
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:558: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:90: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  return self._float_to_str(self.smallest_subnormal)
/usr/local/lib/python3.11/site-packages/numpy/_core/getlimits.py:558: UserWarning: The value of the smallest subnormal for <class 'numpy.float64'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/usr/local/lib/python

Processing genomes: 100%|████████████████████████████████████████████████████████████████████| 3/3 [27:59<00:00, 559.68s/it]

Receptor extraction complete. Results saved to /home/sntokos/SerraPHIM/data/inference_data/bakta_results/Bact_receptors_inference.json and /home/sntokos/SerraPHIM/data/inference_data/bakta_results/Bact_receptors_verbose_inference.json


## 7 - Feature construction

In [ ]:
# 7 - FEATURE CONSTRUCTION
# --------------------------------------------------

# ESM-2 features for RBPs
sf.compute_esm2_embeddings_rbp_improved(
    data_inf_path, 
    data_suffix, 
    batch_size=n_cpus
)

Embedding sequences: 100%|██████████████████████████████████████████████████████████████████| 61/61 [03:32<00:00,  3.49s/it]


Saved embeddings to /home/sntokos/SerraPHIM/data/inference_data/esm2_embeddings_rbp_inference.csv


In [ ]:
# ESM-2 features for bacterial receptors 
sf.compute_esm2_embeddings_receptors(
    data_inf_path, 
    bakta_inf_results_path, 
    data_suffix,
    aggregate_by_accession=True,  # Set to true during internship
    batch_size=n_cpus,
    skip_long_seq=False
)

Will process EIF4_310 solo (length=1769 AA)
Will process EIF4_340 solo (length=3271 AA)
Will process EIF4_363 solo (length=3314 AA)
Will process EIF4_370 solo (length=1607 AA)
Will process EIF4_424 solo (length=1960 AA)
Will process LVF3_402 solo (length=1608 AA)
Will process LVF4_297 solo (length=3591 AA)
Will process LVF4_333 solo (length=3282 AA)
Will process LVF4_356 solo (length=3227 AA)


Embedding batches: 100%|██████████████████████████████████████████████████████████████████████| 9/9 [01:05<00:00,  7.33s/it]


Saved embeddings to: /home/sntokos/SerraPHIM/data/inference_data/esm2_embeddings_receptors_inference.csv


In [38]:
def construct_feature_matrices_inference(
    receptor_embeddings_path, 
    rbp_embeddings_path
):
    """
    Constructs feature matrix for inference (no labels), pairing every host with every phage.

    Returns:
    - features: numpy array of concatenated ESM-2 embeddings
    - groups_hosts: list of host accessions (repeated for each phage)
    - groups_phages: list of phage IDs (repeated per host)
    """
    receptor_embeddings = pd.read_csv(receptor_embeddings_path)
    RBP_embeddings = pd.read_csv(rbp_embeddings_path)

    # Average RBP embeddings per phage
    phage_ids = []
    avg_rbps = []
    for phage_id in set(RBP_embeddings['phage_ID']):
        subset = RBP_embeddings[RBP_embeddings['phage_ID'] == phage_id].iloc[:, 2:]
        avg_rbps.append(np.mean(subset.values, axis=0))
        phage_ids.append(phage_id)
    rbp_df = pd.concat([pd.DataFrame({'phage_ID': phage_ids}), pd.DataFrame(avg_rbps)], axis=1)

    # Construct features
    features = []
    groups_hosts = []
    groups_phages = []

    accessions = receptor_embeddings['accession']
    phage_ids = rbp_df['phage_ID']

    for i, acc in enumerate(accessions):
        receptor_emb = receptor_embeddings.iloc[i, 1:].values  # skip 'accession'
        for j, phage_id in enumerate(phage_ids):
            rbp_emb = rbp_df.iloc[j, 1:].values  # skip 'phage_ID'
            combined = np.concatenate([receptor_emb, rbp_emb])
            features.append(combined)
            groups_hosts.append(acc)
            groups_phages.append(phage_id)

    return np.array(features), groups_hosts, groups_phages


In [ ]:
# Construct features
features, groups_hosts, groups_phages = construct_feature_matrices_inference(
    receptor_embeddings_path=f"{data_inf_path}/esm2_embeddings_receptors{data_suffix}.csv",
    rbp_embeddings_path=f"{data_inf_path}/esm2_embeddings_rbp{data_suffix}.csv"
)

## 8 - Predict & rank new interactions

In [ ]:
# 8 - PREDICT & RANK NEW INTERACTIONS
# --------------------------------------------------

# Load the model
model_path = f"{results_path}/xgb_receptor_model_tuned_training.json"

model = XGBClassifier()
model.load_model(model_path)

In [46]:
# Predict
scores = model.predict_proba(features)[:, 1]  # interaction probability

In [47]:
# Unique host and phage IDs
hosts = sorted(set(groups_hosts))
phages = sorted(set(groups_phages))

# Initialize score matrix
score_matrix = np.zeros((len(hosts), len(phages)))

# Map phage index
phage_to_idx = {ph: i for i, ph in enumerate(phages)}
host_to_idx = {h: i for i, h in enumerate(hosts)}

# Fill matrix
for h, p, s in zip(groups_hosts, groups_phages, scores):
    i = host_to_idx[h]
    j = phage_to_idx[p]
    score_matrix[i, j] = s

# Save as DataFrame
results_df = pd.DataFrame(score_matrix, index=hosts, columns=phages)
results_df.to_csv(f"{results_path}/prediction_results{data_suffix}.csv")

In [48]:
# Rank phages per host
ranked = {}
for i, host in enumerate(hosts):
    phage_scores = [(ph, score_matrix[i, phage_to_idx[ph]]) for ph in phages]
    phage_scores.sort(key=lambda x: x[1], reverse=True)
    ranked[host] = phage_scores

# Save rankings
with open(f"{results_path}/ranked_results{data_suffix}.pickle", "wb") as f:
    pickle.dump(ranked, f)

In [56]:
# Load results
with open(f"{results_path}/ranked_results{data_suffix}.pickle", "rb") as f:
    ranked_results = pickle.load(f)

top_n = 15

# Prepare ranked DataFrame
ranked_table = pd.DataFrame(index=results_df.index)

for rank in range(1, top_n + 1):
    phage_names_at_rank = []
    scores_at_rank = []

    for bact in results_df.index:
        # Sort phages by descending score for this bacterium
        top_phages = results_df.loc[bact].sort_values(ascending=False).head(top_n)
        phage = top_phages.index[rank - 1] if len(top_phages) >= rank else None
        score = top_phages.iloc[rank - 1] if len(top_phages) >= rank else None
        phage_names_at_rank.append(phage)
        scores_at_rank.append(round(score, 3) if score is not None else None)

    ranked_table[f"Rank {rank} Phage"] = phage_names_at_rank
    ranked_table[f"Rank {rank} Score"] = scores_at_rank

In [58]:
ranked_table.style.set_sticky().set_table_attributes('style="overflow-x:auto; display:block"')

In [59]:
ranked_table.to_csv(f"{results_path}/top_{top_n}_ranked_phages{data_suffix}.csv")